In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
import os
api_key_openai = os.environ.get('OPENAI_API_KEY')
org_openai = os.environ.get('OPENAI_ORG')

import openai
openai.organization = org_openai
import numpy as np

In [5]:
import os
import sys
import inspect

sys.path.insert(0, '../..')

import pickle

In [6]:
from src.GetEmbeddings.GetEmbeddingsOpenAI import GetEmbeddingsOpenAI

In [7]:
from src.Clustering.Clustering import Clustering_and_DimRed

c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1086: NumbaD

In [8]:
data = pickle.load(open("../../Data/Emebeddings/embeddings_20ng_raw.pkl", "rb"))
embeddings = data["embeddings"]
corpus = data["corpus"]

In [9]:
vocab_embeddings = pickle.load(open("../../Data/Emebeddings/embeddings_20ng_vocab.pkl", "rb"))

In [10]:
clusterer = Clustering_and_DimRed(min_cluster_size_hdbscan = 5, number_clusters_hdbscan = 20)
dim_red_embeddings, clusters, umap_mapper = clusterer.cluster_and_reduce(embeddings)

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0, n_components=5, random_state=42, verbose=True)
Fri Aug  4 11:57:21 2023 Construct fuzzy simplicial set
Fri Aug  4 11:57:21 2023 Finding Nearest Neighbors
Fri Aug  4 11:57:21 2023 Building RP forest with 12 trees
Fri Aug  4 11:57:26 2023 NN descent for 14 iterations
	 1  /  14
	 2  /  14
	 3  /  14
	 4  /  14
	 5  /  14
	 6  /  14
	Stopping threshold met -- exiting after 6 iterations
Fri Aug  4 11:57:51 2023 Finished Nearest Neighbor Search
Fri Aug  4 11:57:54 2023 Construct embedding


Epochs completed: 100%| ██████████ 200/200 [00:13]


Fri Aug  4 11:58:08 2023 Finished embedding


In [11]:
clusterer.visualize_clusters_dynamic(dim_red_embeddings, clusters, corpus)

In [12]:
#visuslize clusters
#clusterer.visualize_clusters_dynamic(dim_red_embeddings, clusters, texts= corpus)

In [13]:
import ExtractTopWords
extractor = ExtractTopWords.ExtractTopWords()

c:\Users\arik_\Documents\Dokumente\Studium\Master\LLM_seminar\Project\src


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [14]:
centroid_dict = extractor.extract_centroids(dim_red_embeddings, clusters)

In [15]:
extractor.compute_centroid_similarity(dim_red_embeddings, extractor.extract_centroids(dim_red_embeddings, clusters), 0)

array([0.00610244, 0.0072777 , 0.00557646, ..., 0.00731738, 0.00708943,
       0.00680215], dtype=float32)

In [16]:
vocab = extractor.compute_corpus_vocab(corpus, min_freq = 0.3, max_freq=0.9)

Processing corpus: 100%|██████████| 18466/18466 [00:31<00:00, 584.65it/s]


Most common words:
n't: 17117
would: 10872
one: 10144
people: 6442
like: 6409
get: 5815
know: 5742
also: 5589
use: 4989
think: 4981


In [17]:
len(vocab)

20775

In [18]:
words_per_topic = extractor.compute_words_topics(corpus, vocab, clusters)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Computing words per topic: 100%|██████████| 18466/18466 [00:17<00:00, 1028.14it/s]


In [19]:
np.unique(clusters)

array([-1,  0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15,
       16, 17, 18, 19], dtype=int64)

In [1]:
tws, tdfidfs = extractor.extract_topwords_tfidf(corpus, vocab, clusters, top_n_words=10)

NameError: name 'extractor' is not defined

In [21]:
# convert top-word dict to matrix of shape (n_topics, n_top_words)
output_tfidf = {
    "topics":np.array(list(tws.values())),
    "topic-word-matrix": tdfidfs.transpose()
}

In [22]:
tws2, cosine_similarity= extractor.extract_top_words_centroid_similarity(vocab, vocab_embeddings, centroid_dict, umap_mapper)

Fri Aug  4 12:00:24 2023 Worst tree score: 0.35134842
Fri Aug  4 12:00:24 2023 Mean tree score: 0.36268457
Fri Aug  4 12:00:24 2023 Best tree score: 0.37967075
Fri Aug  4 12:00:28 2023 Forward diversification reduced edges from 276990 to 99863
Fri Aug  4 12:00:31 2023 Reverse diversification reduced edges from 99863 to 99863


c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\scipy\sparse\_index.py:143: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



Fri Aug  4 12:00:35 2023 Degree pruning reduced edges from 114512 to 112287
Fri Aug  4 12:00:35 2023 Resorting data and graph based on tree order
Fri Aug  4 12:00:35 2023 Building and compiling search function


Epochs completed: 100%| ██████████ 30/30 [00:02]


In [23]:
output_cos = {
    "topics": np.array(list(tws2.values())),
    "topic-word_matrix": cosine_similarity
}

In [63]:
import Evaluation.Metrics as metrics
from sentence_transformers import SentenceTransformer

In [31]:
emb_dict = metrics.Embed_vocab(vocab, embedder = SentenceTransformer("paraphrase-MiniLM-L6-v2"), emb_filename= "vocab_embedding_20ng_minilml6", emb_path = "../Evaluation/Embeddings/")

In [32]:
Embedding_Coherence = metrics.Embedding_Coherence(corpus_dict = emb_dict)

In [33]:
r1 = Embedding_Coherence.score(output_tfidf)

100%|██████████| 20/20 [00:00<00:00, 19812.49it/s]


In [84]:
NPMI = metrics.NPMI_coherence_gensim(corpus, vocab, coherence = "u_mass")

In [85]:
from gensim.test.utils import common_corpus, common_dictionary

In [88]:
NPMI.score(output_tfidf)

[[(0, 1), (1, 1), (2, 1), (3, 1)], [(4, 2)], [(5, 1), (6, 1)], [(7, 1), (8, 1), (9, 1), (10, 1), (11, 1)], [(12, 1), (13, 1), (14, 1), (15, 1)], [(16, 1), (17, 1), (18, 1)], [], [(19, 1), (20, 1), (21, 1), (22, 1)], [(23, 1)], [(24, 1)], [(25, 1)], [(26, 1), (27, 1)], [(28, 1), (29, 1), (30, 1), (31, 2), (32, 1), (33, 1), (34, 1), (35, 2), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 1), (59, 1), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1)], [(65, 1)], [(66, 1)], [(67, 1), (68, 1), (69, 1), (70, 1), (71, 1), (72, 1)], [(73, 2), (74, 1)], [(75, 1), (76, 1), (77, 1)], [(78, 1), (79, 1), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 1)], [(95, 1), (96, 1), (97, 1), (98, 1), (99, 1)], [(100, 1), (101, 2), (102, 1), (103, 1), (104, 1), (105, 1), (106, 

-16.598608446923343